In [16]:
import pandas as pd
import json
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from xgboost import XGBClassifier
from sklearn.metrics import accuracy_score
from sklearn import preprocessing

df = pd.read_json('PDB_profiles_votes.json')

In [17]:
sample = df.sample(10000).reset_index(drop=True).set_index('name')
sample

mbti_votes  \
name                                                                    
Tom Brokaw          [{'myValue': 'INTP', 'personality_system_id': ...   
Joyce Monroe        [{'myValue': 'ESFP', 'personality_system_id': ...   
Martin Qwerly       [{'myValue': 'ENFP', 'personality_system_id': ...   
Chris Stein         [{'myValue': 'ENFP', 'personality_system_id': ...   
Frank Abagnale Sr.  [{'myValue': 'ESFJ', 'personality_system_id': ...   
...                                                               ...   
Ignus               [{'myValue': 'ISFP', 'personality_system_id': ...   
Qilby               [{'myValue': 'INFJ', 'personality_system_id': ...   
Martin              [{'myValue': 'ESFP', 'personality_system_id': ...   
Suzuka Dairenji     [{'myValue': 'ESTP', 'personality_system_id': ...   
Georgia Thomas      [{'myValue': 'ESFJ', 'personality_system_id': ...   

                                                          ngram_votes  \
name                                                                    
Tom Brokaw          [{'myValue': '5w6', 'personality_system_id': 2...   
Joyce Monroe        [{'myValue': '7w8', 'personality_system_id': 2...   
Martin Qwerly       [{'myValue': '7w6', 'personality_system_id': 2...   
Chris Stein         [{'myValue': '5w6', 'personality_system_id': 2...   
Frank Abagnale Sr.  [{'myValue': '3w2', 'personality_system_id': 2...   
...                                                               ...   
Ignus               [{'myValue': '7w8', 'personality_system_id': 2...   
Qilby               [{'myValue': '6w5', 'personality_system_id': 2...   
Martin              [{'myValue': '7w6', 'personality_system_id': 2...   
Suzuka Dairenji     [{'myValue': '8w7', 'personality_system_id': 2...   
Georgia Thomas      [{'myValue': 'XXXX', 'personality_system_id': ...   

                                                      socionics_votes  \
name                                                                    
Tom Brokaw          [{'myValue': 'ILE', 'personality_system_id': 3...   
Joyce Monroe        [{'myValue': 'ESE', 'personality_system_id': 3...   
Martin Qwerly       [{'myValue': 'XXXX', 'personality_system_id': ...   
Chris Stein         [{'myValue': 'XXXX', 'personality_system_id': ...   
Frank Abagnale Sr.  [{'myValue': 'ESE', 'personality_system_id': 3...   
...                                                               ...   
Ignus               [{'myValue': 'EIE', 'personality_system_id': 3...   
Qilby               [{'myValue': 'EII', 'personality_system_id': 3...   
Martin              [{'myValue': 'XXXX', 'personality_system_id': ...   
Suzuka Dairenji     [{'myValue': 'SEE', 'personality_system_id': 3...   
Georgia Thomas      [{'myValue': 'XXXX', 'personality_system_id': ...   

                                                     alignement_votes  \
name                                                                    
Tom Brokaw          [{'myValue': 'Lawful Good', 'personality_syste...   
Joyce Monroe        [{'myValue': 'Lawful Evil', 'personality_syste...   
Martin Qwerly       [{'myValue': 'XXXX', 'personality_system_id': ...   
Chris Stein         [{'myValue': 'XXXX', 'personality_system_id': ...   
Frank Abagnale Sr.  [{'myValue': 'XXXX', 'personality_system_id': ...   
...                                                               ...   
Ignus               [{'myValue': 'XXXX', 'personality_system_id': ...   
Qilby               [{'myValue': 'Lawful Neutral', 'personality_sy...   
Martin              [{'myValue': 'XXXX', 'personality_system_id': ...   
Suzuka Dairenji     [{'myValue': 'Chaotic Evil', 'personality_syst...   
Georgia Thomas      [{'myValue': 'XXXX', 'personality_system_id': ...   

                                                 instintual_var_votes  \
name                                                                    
Tom Brokaw          [{'myValue': 'sx/sp', 'personality_system_id':...   
Joyce Monroe        [{'myValue': 'sx/so'

In [18]:
# Initialize an empty dictionary to store dataframes for each type of count
all_data_df = {}

# Assuming `sample` is a DataFrame with columns for each type of vote data
for col in sample.columns:
    vote_counts = {}
    for row, votes in enumerate(sample[col]):
        character = sample.index[row]
        vote_counts[character] = {vote['myValue']: vote['theCount'] for vote in votes}
    
    # Convert vote_counts to a DataFrame
    vote_counts_df = pd.DataFrame(vote_counts).transpose()
    
    # Store the DataFrame in the all_data_df dictionary
    all_data_df[col] = vote_counts_df

# Access each DataFrame by the type of count
mbti_counts_df = all_data_df['mbti_votes'].drop(columns = 'XXXX')
enneagram_counts_df = all_data_df['ngram_votes'].drop(columns = 'XXXX')
socionics_counts_df = all_data_df['socionics_votes'].drop(columns = 'XXXX')
alignement_counts_df = all_data_df['alignement_votes'].drop(columns = 'XXXX')
instinctual_variant_counts_df = all_data_df['instintual_var_votes'].drop(columns = 'XXXX')
tritype_counts_df = all_data_df['tritype_votes'].drop(columns = 'XXXX')
temperaments_counts_df = all_data_df['temperament_votes'].drop(columns = 'XXXX')
attitudnal_psyque_counts_df = all_data_df['attitudnal_psyque_votes'].drop(columns = 'XXXX')
big5_counts_df = all_data_df['big5_votes'].drop(columns = 'XXXX')

# If you want to combine all DataFrames into one, you can use the following:
combined_df = pd.concat(all_data_df, axis=1)

In [ ]:
def get_most_likely_mbti(mbti_df):
    
    mbti_df['prob_E'] = None
    mbti_df['prob_N'] = None
    mbti_df['prob_T'] = None
    mbti_df['prob_P'] = None
    mbti_df['prob_MBTI'] = None
    for row in range(len(mbti_df)):
        df1 = mbti_df.iloc[row].to_frame().rename(columns={mbti_df.iloc[row].to_frame().columns[0]: 'votes'})
        df1['E_I'] = df1.index.str[0]
        if df1['votes'].sum() <= 10:
            continue
        # Count occurrences of E and I
        prob_E = df1[df1['E_I'] == 'E']['votes'].sum()/df1['votes'].sum()
        prob_I = df1[df1['E_I'] == 'I']['votes'].sum()/df1['votes'].sum()
        mbti_df['prob_E'].iloc[row] = prob_E

        df1['N_S'] = df1.index.str[1]
        # Count occurrences of N and S
        prob_N = df1[df1['N_S'] == 'N']['votes'].sum()/df1['votes'].sum()
        prob_S = df1[df1['N_S'] == 'S']['votes'].sum()/df1['votes'].sum()
        mbti_df['prob_N'].iloc[row] = prob_N

        df1['T_F'] = df1.index.str[2]
        # Count occurrences of T and F
        prob_T = df1[df1['T_F'] == 'T']['votes'].sum()/df1['votes'].sum()
        prob_F = df1[df1['T_F'] == 'F']['votes'].sum()/df1['votes'].sum()
        mbti_df['prob_T'].iloc[row] = prob_T

        df1['P_J'] = df1.index.str[3]
        # Count occurrences of P and J
        prob_P = df1[df1['P_J'] == 'P']['votes'].sum()/df1['votes'].sum()
        prob_J = df1[df1['P_J'] == 'J']['votes'].sum()/df1['votes'].sum()
        mbti_df['prob_P'].iloc[row] = prob_P

        personality = ''
        if prob_E >= 0.5:
            personality+='E'
        else:
            personality+='I'

        if prob_N >= 0.5:
            personality+='N'
        else:
            personality+='S'

        if prob_T >= 0.5:
            personality+='T'
        else:
            personality+='F'

        if prob_P >= 0.5:
            personality+='P'
        else:
            personality+='J'

        mbti_df['prob_MBTI'].iloc[row] = personality

    return mbti_df



def get_most_likely_enneagram(enneagram_df):
    
    new_enneagram_df = enneagram_df.copy()
    new_enneagram_df['prob_1'] = None
    new_enneagram_df['prob_2'] = None
    new_enneagram_df['prob_3'] = None
    new_enneagram_df['prob_4'] = None
    new_enneagram_df['prob_5'] = None
    new_enneagram_df['prob_6'] = None
    new_enneagram_df['prob_7'] = None
    new_enneagram_df['prob_8'] = None
    new_enneagram_df['prob_9'] = None
    new_enneagram_df['prob_Enneagram'] = None
    
    for row in range(len(new_enneagram_df)):
        
        
        df1 = new_enneagram_df.iloc[row].to_frame().rename(columns={new_enneagram_df.iloc[row].to_frame().columns[0]: 'votes'})
        
        if df1['votes'].sum() <= 10:
            continue

        wings = list(df1.index)
        prob_max = []
        for i in range(1, 10):
            votes_for_i = df1.loc[df1.index.str[0].isin([f'{i}']), 'votes'].sum()
            new_enneagram_df[f'prob_{i}'].iloc[row] = votes_for_i / df1['votes'].sum()
            prob_max.append([i,  new_enneagram_df[f'prob_{i}'].iloc[row]])

        most_likely_type = max(prob_max, key=lambda x: x[1])[0]
        most_likely_type_votes = df1.loc[df1.index.str.startswith(f'{most_likely_type}'), 'votes'].to_dict()
        most_likely_enneagram = max(most_likely_type_votes, key=most_likely_type_votes.get)
        new_enneagram_df['prob_Enneagram'].iloc[row] = most_likely_enneagram

    return new_enneagram_df

def get_most_likely_socionics(df):
    # Initialize columns for probabilities and the most likely Socionics type
    socionics_df = df.copy()
    socionics_df['prob_Socionics'] = None
    
    for row in range(len(socionics_df)):
        df1 = socionics_df.iloc[row].to_frame().rename(columns={socionics_df.iloc[row].to_frame().columns[0]: 'votes'})
        print(row)
        if df1['votes'].sum() <= 10:
            continue
        values = ['E', 'I', 'S', 'L']
        prob_max = []
        for i in values:
            votes_for_i = df1.loc[df1.index.str[0].isin([f'{i}']), 'votes'].sum()
            prob_max.append([i,   votes_for_i / df1['votes'].sum()] )

        most_likely_type = max(prob_max, key=lambda x: x[1])[0]
        most_likely_type_votes = df1.loc[df1.index.str[0].isin([most_likely_type]), 'votes'].to_dict()
        prob_max2 = []
        for j in values:
        
            votes_for_i2 = df1.loc[most_likely_type_votes.keys()].loc[df1.loc[most_likely_type_votes.keys()].index.str[1].isin([f'{j}']), 'votes'].sum()
            #print( prob_max, most_likely_type, votes_for_i2 )
            prob_max2.append([j,   votes_for_i2 / df1.loc[most_likely_type_votes.keys()]['votes'].sum()] )


        most_likely_type2 = max(prob_max2, key=lambda x: x[1])[0]
        most_likely_type_votes2 = df1.loc[most_likely_type_votes.keys()].loc[df1.loc[most_likely_type_votes.keys()].index.str[1].isin([most_likely_type2]), 'votes'].to_dict()
        socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)  
    
    return socionics_df

new_socionics_df = get_most_likely_socionics(socionics_counts_df)
new_enneagram_df = get_most_likely_enneagram(enneagram_counts_df)
new_mbti_df = get_most_likely_mbti(mbti_df = mbti_counts_df)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37


C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docum

38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86


C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docum

87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124


...

C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docum

1937
1938
1939
1940
1941
1942
1943
1944
1945
1946
1947
1948
1949
1950
1951
1952
1953
1954
1955
1956
1957
1958
1959
1960
1961
1962
1963
1964
1965
1966
1967
1968
1969
1970
1971
1972
1973


C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  socionics_df['prob_Socionics'].iloc[row] = max(most_likely_type_votes2, key=most_likely_type_votes2.get)
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:127: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the docum

1974
1975
1976
1977
1978
1979
1980
1981
1982
1983
1984
1985
1986
1987
1988
1989


C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:89: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_enneagram_df[f'prob_{i}'].iloc[row] = votes_for_i / df1['votes'].sum()
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:89: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_enneagram_df[f'prob_{i}'].iloc[row] = votes_for_i / df1['votes'].sum()
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3347411535.py:89: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_gui

In [ ]:
# Assuming 'df' is your original dataframe
# Use idxmax to find the index of maximum value across rows (MBTI type with most votes)
a = [alignement_counts_df, instinctual_variant_counts_df, tritype_counts_df, 
     temperaments_counts_df,attitudnal_psyque_counts_df, big5_counts_df]
counts = []
prob_traits_df = pd.DataFrame()
for df in a:
    max_votes = df.T.idxmax()
    # Create a new dataframe using these indices
    result_df = pd.DataFrame(max_votes).transpose()
    prob_traits_df = pd.concat([prob_traits_df, result_df])
    counts.append(result_df.T.value_counts())

C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3469824595.py:8: FutureWarning: The behavior of DataFrame.idxmax with all-NA values, or any-NA and skipna=False, is deprecated. In a future version this will raise ValueError
  max_votes = df.T.idxmax()
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3469824595.py:8: FutureWarning: The behavior of DataFrame.idxmax with all-NA values, or any-NA and skipna=False, is deprecated. In a future version this will raise ValueError
  max_votes = df.T.idxmax()
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3469824595.py:8: FutureWarning: The behavior of DataFrame.idxmax with all-NA values, or any-NA and skipna=False, is deprecated. In a future version this will raise ValueError
  max_votes = df.T.idxmax()
C:\Users\caoco\AppData\Local\Temp\ipykernel_3660\3469824595.py:8: FutureWarning: The behavior of DataFrame.idxmax with all-NA values, or any-NA and skipna=False, is deprecated. In a future version this will raise ValueError
  max_votes = df.T.i

In [ ]:
prob_traits_df = pd.concat([new_socionics_df['prob_Socionics'].to_frame().T, prob_traits_df])
prob_traits_df = pd.concat([new_enneagram_df['prob_Enneagram'].to_frame().T, prob_traits_df])
prob_traits_df = pd.concat([new_mbti_df['prob_MBTI'].to_frame().T, prob_traits_df])

In [ ]:
traits_df = prob_traits_df.T.dropna()
traits_df = traits_df.T.reset_index(drop=True).T
traits_df = traits_df.rename(columns={0:'mbti', 1:'ngram', 2: 'socionics', 3: 'moral_alignement',
                         4: 'instintual_var', 5: 'tritype', 6: 'temperament', 7: 'attitudinal_psyque', 8:'big5'})

traits_df

mbti ngram socionics moral_alignement  \
Thomas Leroy / The Gentleman  ENTJ   8w7       LII     Neutral Evil   
Doc Hudson                    ISTJ   5w4       LSI   Lawful Neutral   
Sherlock Holmes               ENTP   5w6       ILE  Chaotic Neutral   
Orochimaru                    ENTP   5w4       ILE     Chaotic Evil   
Arsène Lupin III              ENTP   7w8       ILE     Chaotic Good   
...                            ...   ...       ...              ...   
Tonpa                         ESTP   7w8       ESI     Chaotic Evil   
Sigmund Freud                 ISTJ   6w5       LSI     True Neutral   
John Locke                    INFJ   4w5       IEI     True Neutral   
Clemont (Citron)              INTP   9w1       ILE      Lawful Good   
Umi Sonoda                    ISTJ   6w5       LSI   Lawful Neutral   

                             instintual_var tritype             temperament  \
Thomas Leroy / The Gentleman          sx/so     837     Choleric [Dominant]   
Doc Hudson                            sp/sx     513  Melancholic [Dominant]   
Sherlock Holmes                       sp/so     531    Melancholic-Choleric   
Orochimaru                            sp/sx     548       Choleric-Sanguine   
Arsène Lupin III                      sp/sx     784    Sanguine-Melancholic   
...                                     ...     ...                     ...   
Tonpa                                 sp/so     783     Sanguine [Dominant]   
Sigmund Freud                         sp/sx     614    Melancholic-Choleric   
John Locke                            sp/so     459    Melancholic-Choleric   
Clemont (Citron)                      so/sp     952   Phlegmatic [Dominant]   
Umi Sonoda                            so/sp     613    Melancholic-Choleric   

                             attitudinal_psyque   big5  
Thomas Leroy / The Gentleman               VFLE  SLOEN  
Doc Hudson                                 LFVE  RCOEN  
Sherlock Holmes                            VLEF  RCUEI  
Orochimaru                                 FLVE  RLUEI  
Arsène Lupin III                           LEVF  SCUEI  
...                                         ...    ...  
Tonpa                                      FLVE  SCUEN  
Sigmund Freud                              LVFE  RCOEI  
John Locke                                 LEVF  RLOEI  
Clemont (Citron)                           LEFV  RLOAI  
Umi Sonoda                                 LFVE  RLOAI  

[371 rows x 9 columns]

from collections import Counter
import plotly.express as px

# Create scatter plots for each categorical column
x_col = 'mbti'
for col in traits_df.select_dtypes(include='object').columns[1:]:
    if col == x_col:
        continue  # Skip this iteration
    print(col)
    # Calculate the count of each unique pair (A, B)
    #col = 'big5'
    counts = Counter(zip(traits_df[x_col], traits_df[col]))
    size_df = traits_df[[x_col, col]].copy()

    # Create a new column 'size' with the count for each pair
    size_df['size'] = [counts[(a, b)] for a, b in zip(size_df[x_col], size_df[col])]

    # Define the desired order for 'mbti' labels
    #custom_order = ['ENFP', 'ESFP', 'ENTP', 'ENFJ', 'ESFJ', 'ESTP', 'ENTJ', 'ESTJ', 'ISTJ', 'INTJ', 'ISTP', 'ISFP', 'INFP', 'INFJ', 'INTP', 'ISFJ']
    custom_order = sorted(size_df[x_col].unique())
    
    # Apply the custom order to the DataFrame
    size_df[x_col] = pd.Categorical(size_df[x_col], categories=custom_order, ordered=True)

    # Define the y-axis ordering
    content_order = sorted(size_df[col].unique())
    #size_df[col] = pd.Categorical(size_df[col], categories=content_order, ordered=True)


    size_df.sort_values(by=x_col, inplace=True)
    # Create the scatter plot
    fig = px.scatter(size_df, x=x_col, y=col, size='size', title=f'Scatter Plot for {x_col} vs. {col}')

    # Set y-axis ticks to match the custom order
    fig.update_yaxes(tickvals=list(range(len(content_order))), ticktext=content_order)

    # Update the layout to set the figure size and background color
    fig.update_layout(
        autosize=False,
        width=800,
        height=600,
        margin=dict(l=50, r=50, b=100, t=100, pad=4),
        paper_bgcolor="LightSteelBlue",
    )

    fig.show()


In [ ]:
traits_df

mbti ngram socionics moral_alignement  \
Thomas Leroy / The Gentleman  ENTJ   8w7       LII     Neutral Evil   
Doc Hudson                    ISTJ   5w4       LSI   Lawful Neutral   
Sherlock Holmes               ENTP   5w6       ILE  Chaotic Neutral   
Orochimaru                    ENTP   5w4       ILE     Chaotic Evil   
Arsène Lupin III              ENTP   7w8       ILE     Chaotic Good   
...                            ...   ...       ...              ...   
Tonpa                         ESTP   7w8       ESI     Chaotic Evil   
Sigmund Freud                 ISTJ   6w5       LSI     True Neutral   
John Locke                    INFJ   4w5       IEI     True Neutral   
Clemont (Citron)              INTP   9w1       ILE      Lawful Good   
Umi Sonoda                    ISTJ   6w5       LSI   Lawful Neutral   

                             instintual_var tritype             temperament  \
Thomas Leroy / The Gentleman          sx/so     837     Choleric [Dominant]   
Doc Hudson                            sp/sx     513  Melancholic [Dominant]   
Sherlock Holmes                       sp/so     531    Melancholic-Choleric   
Orochimaru                            sp/sx     548       Choleric-Sanguine   
Arsène Lupin III                      sp/sx     784    Sanguine-Melancholic   
...                                     ...     ...                     ...   
Tonpa                                 sp/so     783     Sanguine [Dominant]   
Sigmund Freud                         sp/sx     614    Melancholic-Choleric   
John Locke                            sp/so     459    Melancholic-Choleric   
Clemont (Citron)                      so/sp     952   Phlegmatic [Dominant]   
Umi Sonoda                            so/sp     613    Melancholic-Choleric   

                             attitudinal_psyque   big5  
Thomas Leroy / The Gentleman               VFLE  SLOEN  
Doc Hudson                                 LFVE  RCOEN  
Sherlock Holmes                            VLEF  RCUEI  
Orochimaru                                 FLVE  RLUEI  
Arsène Lupin III                           LEVF  SCUEI  
...                                         ...    ...  
Tonpa                                      FLVE  SCUEN  
Sigmund Freud                              LVFE  RCOEI  
John Locke                                 LEVF  RLOEI  
Clemont (Citron)                           LEFV  RLOAI  
Umi Sonoda                                 LFVE  RLOAI  

[371 rows x 9 columns]

In [ ]:
# data is a Pandas DataFrame
# Assuming 'traits_df' contains your dataset with features and target variable ('ngram')
df = traits_df.copy()
df['is_E'] = np.where(df['mbti'].str[0] == 'E', True, False)
#df['is_N'] = np.where(df['mbti'].str[1] == 'N', True, False)
#df['is_T'] = np.where(df['mbti'].str[2] == 'T', True, False)
#df['is_P'] = np.where(df['mbti'].str[3] == 'P', True, False)


# Encode categorical variables
for col in df.columns:
    if df[col].dtype == 'object':
        df[col] = df[col].astype('category')


from collections import defaultdict
d = defaultdict(preprocessing.LabelEncoder)

# Encoding the variable
df_fit = df.apply(lambda x: d[x.name].fit_transform(x))

# Inverse the encoded (df_i = df)
df_i = df_fit.apply(lambda x: d[x.name].inverse_transform(x))

# Using the dictionary to label future data
#df.apply(lambda x: d[x.name].transform(x))


# Split data into train and test sets
target = 'is_E'
remove = ['mbti', 'socionics', 'attitudinal_psyque', 'big5']
X = df_fit.drop(columns=[target]+remove)
y = df_fit[target]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Train Random Forest model
rf_model = RandomForestClassifier(n_estimators=20, random_state=42)
rf_model.fit(X_train, y_train)

# Train XGBoost model
xgb_model = XGBClassifier(n_estimators=10, random_state=42)
xgb_model.fit(X_train, y_train)

# Evaluate models
rf_preds = rf_model.predict(X_test)
rf_accuracy = accuracy_score(y_test, rf_model.predict(X_test))

xgb_preds = xgb_model.predict(X_test)
xgb_accuracy = accuracy_score(y_test, xgb_model.predict(X_test))
print(f"Random Forest Accuracy: {rf_accuracy:.4f}")
print(f"XGBoost Accuracy: {xgb_accuracy:.4f}")


le = preprocessing.LabelEncoder()
df[target].to_frame().apply(le.fit_transform)
predicted_results = le.inverse_transform(xgb_preds)

test_df = X_test.apply(lambda x: d[x.name].inverse_transform(x))
test_df[target] = le.inverse_transform(y_test)
test_df[f'predicted_{target}'] = predicted_results
#fit.apply(xgb_preds.inverse_transform())

Random Forest Accuracy: 0.8000
XGBoost Accuracy: 0.7733
